In [1]:
# Para usar o sleep:
import time
# Para logs:
from tqdm import tqdm
import logging
import sys
sys.path.append('../utils')
from utils import get_logger, load_json, export_json, Clock
# Para web scraping:
import requests
from bs4 import BeautifulSoup, SoupStrainer
import cchardet
# Para acessar as credenciais de login de um arquivo externo:
import os
import dotenv
# Para navegar na página além do botão 'Show more':
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait 
from selenium.webdriver.support import expected_conditions as EC
# Contador
from itertools import count
# Manipulação de JSON:
import json
from dictdiffer import diff
# Para calcular similaridade entre strings:
from thefuzz import fuzz

Inicializando o logger:

In [2]:
logger = logging.getLogger(__name__)
logger = get_logger(logger=logger)

Carregando as credenciais de acesso ao _Untappd_:

In [3]:
dotenv.load_dotenv()
EMAIL = os.getenv('EMAIL')
PASSWORD = os.getenv('PASSWORD')

Definindo as opções do navegador que o Selenium usará:

In [4]:
options = Options()
options.add_argument("--disable-infobars")
options.add_argument("start-maximized")
options.add_argument("--disable-extensions")
options.add_experimental_option("prefs", {"profile.default_content_setting_values.notifications": 1})

Definindo os parâmetros da request:

In [5]:
base_url = 'https://untappd.com'
headers = {
    'User-Agent':
    'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/111.0.0.0 Safari/537.36 OPR/97.0.0.0'
}

Abrindo o navegador, acessando a página de _login_, inserindo as credenciais e aguardando 30 segundos para a resolução manual do reCAPTCHA:

In [6]:
browser = webdriver.Chrome(options=options)
browser.get(base_url + '/login')
browser.find_element(By.NAME,"username").send_keys(EMAIL)
browser.find_element(By.NAME,"password").send_keys(PASSWORD)
time.sleep(30)

Buscando por 'brazil' na seção de cervejarias do _Untappd_ e clicando no link de 'Show more' até alcançar o final da página:

In [7]:
wait = WebDriverWait(browser, 10)

browser.get(base_url + '/search?q=brazil&type=brewery')
counter = count(1)
while True:
    try:
        element = wait.until(EC.element_to_be_clickable((By.CSS_SELECTOR, "[data-href=':more_brewery']")))
        browser.execute_script("arguments[0].click();", element)
        time.sleep(5)
        logger.info(f"Link 'Show more' da página de cervejarias clicado pela {next(counter)}ª vez...")
    except:
        logger.info("Fim da página alcançado!")
        break
        
full_page = browser.page_source

2023-09-22 21:16:34,505 - INFO - Link 'Show more' da página de cervejarias clicado pela 1ª vez...
2023-09-22 21:16:39,558 - INFO - Link 'Show more' da página de cervejarias clicado pela 2ª vez...
2023-09-22 21:16:44,614 - INFO - Link 'Show more' da página de cervejarias clicado pela 3ª vez...
2023-09-22 21:16:49,669 - INFO - Link 'Show more' da página de cervejarias clicado pela 4ª vez...
2023-09-22 21:16:54,720 - INFO - Link 'Show more' da página de cervejarias clicado pela 5ª vez...
2023-09-22 21:16:59,782 - INFO - Link 'Show more' da página de cervejarias clicado pela 6ª vez...
2023-09-22 21:17:04,836 - INFO - Link 'Show more' da página de cervejarias clicado pela 7ª vez...
2023-09-22 21:17:09,891 - INFO - Link 'Show more' da página de cervejarias clicado pela 8ª vez...
2023-09-22 21:17:14,949 - INFO - Link 'Show more' da página de cervejarias clicado pela 9ª vez...
2023-09-22 21:17:20,000 - INFO - Link 'Show more' da página de cervejarias clicado pela 10ª vez...
2023-09-22 21:17:25

In [8]:
logger.info("Coletando links que levam às listas de cervejas das cervejarias brasileiras...")
soup = BeautifulSoup(full_page, 'html.parser')
brewery_beer_list_links = [a_tag.get('href') + '/beer' for a_tag in soup.select('div.beer-item > a.label')]
logger.info(f"Feito! Foram coletados {len(brewery_beer_list_links)} links.")

2023-09-22 21:20:02,375 - INFO - Coletando links que levam às listas de cervejas das cervejarias brasileiras...
2023-09-22 21:20:03,519 - INFO - Feito! Foram coletados 1000 links.


In [19]:
all_beers = set()
logger.info("Iniciando uma sessão...")
with requests.Session() as session:
    logger.info("A iteração começará agora...")
    iteration_time = Clock("Coleta dos IDs de usuários")
    with tqdm(total=len(brewery_beer_list_links)) as progress_bar:
        progress_bar.set_description("Coletando os links de todas as cervejas das cervejarias da lista...")
        wait = WebDriverWait(browser, 10)
        page_counter = count(1)
        for beer_list_url in brewery_beer_list_links:
            browser.get(base_url + beer_list_url)
            counter = count(1)
            while True:
                try:
                    element = wait.until(EC.element_to_be_clickable((By.CSS_SELECTOR, "[data-href=':more_beer']")))
                    browser.execute_script("arguments[0].click();", element)
                    time.sleep(5)
                    logger.info(f"Link 'Show more' da {str(page_counter)[6:-1]}ª página clicado pela {next(counter)}ª vez")
                except:
                    logger.info('Fim da página alcançado!')
                    next(page_counter)
                    break
            full_page = browser.page_source
            a_tag = SoupStrainer('a')
            soup = BeautifulSoup(full_page, 'html.parser', parse_only=a_tag)
            beers = set(link.get('href') for link in soup.select("a[href^='/b/']"))
            all_beers.update(beers)
            logger.info(f"Foram coletadas {len(beers)} cervejas da página completa.")
            progress_bar.update(1)
    iteration_time.stop_watch()
    logger.info("Coleta concluída!")
logger.info(f'No total foram coletadas {len(all_beers)} cervejas!')

2023-09-23 08:51:07,741 - INFO - Iniciando uma sessão...
2023-09-23 08:51:07,743 - INFO - A iteração começará agora...
Coletando os links de todas as cervejas das cervejarias da lista...:   0%|                    | 0/1000 [00:00<?, ?it/s]2023-09-23 08:51:17,770 - INFO - Link 'Show more' da 1ª página clicado pela 1ª vez
2023-09-23 08:51:22,825 - INFO - Link 'Show more' da 1ª página clicado pela 2ª vez
2023-09-23 08:51:27,884 - INFO - Link 'Show more' da 1ª página clicado pela 3ª vez
2023-09-23 08:51:32,950 - INFO - Link 'Show more' da 1ª página clicado pela 4ª vez
2023-09-23 08:51:38,011 - INFO - Link 'Show more' da 1ª página clicado pela 5ª vez
2023-09-23 08:51:43,072 - INFO - Link 'Show more' da 1ª página clicado pela 6ª vez
2023-09-23 08:51:48,124 - INFO - Link 'Show more' da 1ª página clicado pela 7ª vez
2023-09-23 08:51:53,172 - INFO - Link 'Show more' da 1ª página clicado pela 8ª vez
2023-09-23 08:51:58,242 - INFO - Link 'Show more' da 1ª página clicado pela 9ª vez
2023-09-23 08:5

2023-09-23 08:58:58,830 - INFO - Link 'Show more' da 11ª página clicado pela 7ª vez
2023-09-23 08:59:03,885 - INFO - Link 'Show more' da 11ª página clicado pela 8ª vez
2023-09-23 08:59:08,943 - INFO - Link 'Show more' da 11ª página clicado pela 9ª vez
2023-09-23 08:59:14,005 - INFO - Link 'Show more' da 11ª página clicado pela 10ª vez
2023-09-23 08:59:19,066 - INFO - Link 'Show more' da 11ª página clicado pela 11ª vez
2023-09-23 08:59:24,112 - INFO - Link 'Show more' da 11ª página clicado pela 12ª vez
2023-09-23 08:59:29,176 - INFO - Link 'Show more' da 11ª página clicado pela 13ª vez
2023-09-23 08:59:34,230 - INFO - Link 'Show more' da 11ª página clicado pela 14ª vez
2023-09-23 08:59:39,289 - INFO - Link 'Show more' da 11ª página clicado pela 15ª vez
2023-09-23 08:59:44,347 - INFO - Link 'Show more' da 11ª página clicado pela 16ª vez
2023-09-23 08:59:49,405 - INFO - Link 'Show more' da 11ª página clicado pela 17ª vez
2023-09-23 08:59:54,463 - INFO - Link 'Show more' da 11ª página clic

2023-09-23 09:06:54,761 - INFO - Foram coletadas 13 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   2%|▏        | 20/1000 [15:47<8:07:09, 29.83s/it]2023-09-23 09:07:02,335 - INFO - Link 'Show more' da 21ª página clicado pela 1ª vez
2023-09-23 09:07:07,403 - INFO - Link 'Show more' da 21ª página clicado pela 2ª vez
2023-09-23 09:07:12,448 - INFO - Link 'Show more' da 21ª página clicado pela 3ª vez
2023-09-23 09:07:17,501 - INFO - Link 'Show more' da 21ª página clicado pela 4ª vez
2023-09-23 09:07:22,555 - INFO - Link 'Show more' da 21ª página clicado pela 5ª vez
2023-09-23 09:07:27,615 - INFO - Link 'Show more' da 21ª página clicado pela 6ª vez
2023-09-23 09:07:32,666 - INFO - Link 'Show more' da 21ª página clicado pela 7ª vez
2023-09-23 09:07:43,145 - INFO - Fim da página alcançado!
2023-09-23 09:07:43,281 - INFO - Foram coletadas 172 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   2

2023-09-23 09:14:46,558 - INFO - Link 'Show more' da 32ª página clicado pela 3ª vez
2023-09-23 09:14:51,616 - INFO - Link 'Show more' da 32ª página clicado pela 4ª vez
2023-09-23 09:15:02,053 - INFO - Fim da página alcançado!
2023-09-23 09:15:02,155 - INFO - Foram coletadas 99 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   3%|▎       | 32/1000 [23:54<10:47:54, 40.16s/it]2023-09-23 09:15:09,685 - INFO - Link 'Show more' da 33ª página clicado pela 1ª vez
2023-09-23 09:15:14,734 - INFO - Link 'Show more' da 33ª página clicado pela 2ª vez
2023-09-23 09:15:25,208 - INFO - Fim da página alcançado!
2023-09-23 09:15:25,270 - INFO - Foram coletadas 50 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   3%|▎        | 33/1000 [24:17<9:24:49, 35.05s/it]2023-09-23 09:15:33,209 - INFO - Link 'Show more' da 34ª página clicado pela 1ª vez
2023-09-23 09:15:38,258 - INFO - Link 'Show more' da 34ª página 

2023-09-23 09:22:28,868 - INFO - Fim da página alcançado!
2023-09-23 09:22:29,007 - INFO - Foram coletadas 70 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   5%|▍        | 48/1000 [31:21<7:08:09, 26.99s/it]2023-09-23 09:22:37,150 - INFO - Link 'Show more' da 49ª página clicado pela 1ª vez
2023-09-23 09:22:42,209 - INFO - Link 'Show more' da 49ª página clicado pela 2ª vez
2023-09-23 09:22:47,276 - INFO - Link 'Show more' da 49ª página clicado pela 3ª vez
2023-09-23 09:22:52,335 - INFO - Link 'Show more' da 49ª página clicado pela 4ª vez
2023-09-23 09:23:02,768 - INFO - Fim da página alcançado!
2023-09-23 09:23:02,852 - INFO - Foram coletadas 85 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:   5%|▍        | 49/1000 [31:55<7:40:18, 29.04s/it]2023-09-23 09:23:11,406 - INFO - Link 'Show more' da 50ª página clicado pela 1ª vez
2023-09-23 09:23:16,465 - INFO - Link 'Show more' da 50ª página 

...

2023-09-23 13:46:00,982 - INFO - Foram coletadas 23 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  88%|███████ | 881/1000 [4:54:53<24:34, 12.39s/it]2023-09-23 13:46:12,231 - INFO - Fim da página alcançado!
2023-09-23 13:46:12,247 - INFO - Foram coletadas 7 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  88%|███████ | 882/1000 [4:55:04<23:41, 12.05s/it]2023-09-23 13:46:23,571 - INFO - Fim da página alcançado!
2023-09-23 13:46:23,594 - INFO - Foram coletadas 5 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  88%|███████ | 883/1000 [4:55:15<23:05, 11.84s/it]2023-09-23 13:46:35,528 - INFO - Fim da página alcançado!
2023-09-23 13:46:35,562 - INFO - Foram coletadas 16 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  88%|███████ | 884/1000 [4:55:27<22:57, 11.88s/it]2023-09-23 13:46:47,953 - IN

Coletando os links de todas as cervejas das cervejarias da lista...:  91%|███████▎| 909/1000 [5:01:19<21:21, 14.08s/it]2023-09-23 13:52:39,419 - INFO - Fim da página alcançado!
2023-09-23 13:52:39,433 - INFO - Foram coletadas 0 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  91%|███████▎| 910/1000 [5:01:31<20:12, 13.47s/it]2023-09-23 13:52:46,805 - INFO - Link 'Show more' da 911ª página clicado pela 1ª vez
2023-09-23 13:52:51,852 - INFO - Link 'Show more' da 911ª página clicado pela 2ª vez
2023-09-23 13:53:02,326 - INFO - Fim da página alcançado!
2023-09-23 13:53:02,382 - INFO - Foram coletadas 46 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  91%|███████▎| 911/1000 [5:01:54<24:12, 16.32s/it]2023-09-23 13:53:13,586 - INFO - Fim da página alcançado!
2023-09-23 13:53:13,607 - INFO - Foram coletadas 2 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da

2023-09-23 13:59:18,417 - INFO - Fim da página alcançado!
2023-09-23 13:59:18,455 - INFO - Foram coletadas 25 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  94%|███████▍| 935/1000 [5:08:10<17:54, 16.53s/it]2023-09-23 13:59:29,682 - INFO - Fim da página alcançado!
2023-09-23 13:59:29,709 - INFO - Foram coletadas 11 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  94%|███████▍| 936/1000 [5:08:21<15:56, 14.95s/it]2023-09-23 13:59:41,201 - INFO - Fim da página alcançado!
2023-09-23 13:59:41,227 - INFO - Foram coletadas 7 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  94%|███████▍| 937/1000 [5:08:33<14:36, 13.92s/it]2023-09-23 13:59:49,036 - INFO - Link 'Show more' da 938ª página clicado pela 1ª vez
2023-09-23 13:59:54,078 - INFO - Link 'Show more' da 938ª página clicado pela 2ª vez
2023-09-23 14:00:04,523 - INFO - Fim da página alcançado!

2023-09-23 14:05:47,402 - INFO - Foram coletadas 25 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  96%|███████▋| 962/1000 [5:14:39<08:35, 13.57s/it]2023-09-23 14:05:58,918 - INFO - Fim da página alcançado!
2023-09-23 14:05:58,933 - INFO - Foram coletadas 7 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  96%|███████▋| 963/1000 [5:14:51<07:59, 12.96s/it]2023-09-23 14:06:10,389 - INFO - Fim da página alcançado!
2023-09-23 14:06:10,404 - INFO - Foram coletadas 0 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  96%|███████▋| 964/1000 [5:15:02<07:30, 12.51s/it]2023-09-23 14:06:21,922 - INFO - Fim da página alcançado!
2023-09-23 14:06:21,944 - INFO - Foram coletadas 0 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  96%|███████▋| 965/1000 [5:15:14<07:07, 12.22s/it]2023-09-23 14:06:28,333 - INF

2023-09-23 14:12:17,227 - INFO - Foram coletadas 17 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  99%|███████▉| 991/1000 [5:21:09<01:52, 12.50s/it]2023-09-23 14:12:28,994 - INFO - Fim da página alcançado!
2023-09-23 14:12:29,009 - INFO - Foram coletadas 6 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  99%|███████▉| 992/1000 [5:21:21<01:38, 12.28s/it]2023-09-23 14:12:40,115 - INFO - Fim da página alcançado!
2023-09-23 14:12:40,131 - INFO - Foram coletadas 14 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  99%|███████▉| 993/1000 [5:21:32<01:23, 11.94s/it]2023-09-23 14:12:52,002 - INFO - Fim da página alcançado!
2023-09-23 14:12:52,031 - INFO - Foram coletadas 5 cervejas da página completa.
Coletando os links de todas as cervejas das cervejarias da lista...:  99%|███████▉| 994/1000 [5:21:44<01:11, 11.92s/it]2023-09-23 14:13:04,036 - IN

In [24]:
path = '../data/'
beer_links_json = {'beer links': sorted(all_beers)}
file_name = 'beer_links.json'

logger.info('Exportando a lista de cervejas coletadas na forma de um JSON...')
export_json(beer_links_json, path + file_name)
logger.info('Exportado!')

2023-09-23 14:43:31,339 - INFO - Exportando a lista de cervejas coletadas na forma de um JSON...
2023-09-23 14:43:31,386 - INFO - Exportado!


In [36]:
all_users = set()
logger.info("Iniciando uma sessão...")
with requests.Session() as session:
    logger.info("A iteração começará agora...")
    iteration_time = Clock("Coleta dos IDs de usuários")
    with tqdm(total=len(all_beers)) as progress_bar:
        progress_bar.set_description("Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...")
        wait = WebDriverWait(browser, 10)
        page_counter = count(1)
        for beer_url in all_beers:
            browser.get(base_url + beer_url)
            counter = count(1)
            while True:
                try:
                    element = wait.until(EC.element_to_be_clickable((By.CSS_SELECTOR, "[data-href=':feed/showmore']")))
                    browser.execute_script("arguments[0].click();", element)
                    time.sleep(5)
                    logger.info(f"Link 'Show more' da {str(page_counter)[6:-1]}ª página clicado pela {next(counter)}ª vez")
                except:
                    logger.info('Fim da página alcançado!')
                    next(page_counter)
                    break
            full_page = browser.page_source
            a_tag = SoupStrainer('a')
            soup = BeautifulSoup(full_page, 'html.parser', parse_only=a_tag)
            users = set('/user/' + link.get('href').split('/user/')[1].split('/')[0] for link in soup.select("a[href^='/user/']"))
            all_users.update(users)
            logger.info(f"Foram coletados {len(users)} id's de usuários da página completa.")
            progress_bar.update(1)
    iteration_time.stop_watch()
    logger.info("Coleta concluída!")

2023-09-23 14:54:19,477 - INFO - Iniciando uma sessão...
2023-09-23 14:54:19,478 - INFO - A iteração começará agora...
Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...:   0%|       | 0/35249 [00:00<?, ?it/s]2023-09-23 14:54:28,217 - INFO - Link 'Show more' da 1ª página clicado pela 1ª vez
2023-09-23 14:54:38,652 - INFO - Fim da página alcançado!
2023-09-23 14:54:38,718 - INFO - Foram coletados 54 id's de usuários da página completa.
Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...:   0%| | 1/35249 [00:19<188:21:26, 19.22023-09-23 14:54:47,810 - INFO - Link 'Show more' da 2ª página clicado pela 1ª vez
2023-09-23 14:54:52,859 - INFO - Link 'Show more' da 2ª página clicado pela 2ª vez
2023-09-23 14:54:57,913 - INFO - Link 'Show more' da 2ª página clicado pela 3ª vez
2023-09-23 14:55:08,019 - INFO - Fim da página alcançado!
2023-09-23 14:55:08,096 - INFO - Foram coletados 69 id's de usuários da página completa.
Coletando os IDs 

2023-09-23 15:01:43,367 - INFO - Fim da página alcançado!
2023-09-23 15:01:43,939 - INFO - Foram coletados 314 id's de usuários da página completa.
Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...:   0%| | 15/35249 [07:24<378:24:39, 38.2023-09-23 15:01:51,069 - INFO - Link 'Show more' da 16ª página clicado pela 1ª vez
2023-09-23 15:01:56,117 - INFO - Link 'Show more' da 16ª página clicado pela 2ª vez
2023-09-23 15:02:01,175 - INFO - Link 'Show more' da 16ª página clicado pela 3ª vez
2023-09-23 15:02:06,230 - INFO - Link 'Show more' da 16ª página clicado pela 4ª vez
2023-09-23 15:02:11,280 - INFO - Link 'Show more' da 16ª página clicado pela 5ª vez
2023-09-23 15:02:16,345 - INFO - Link 'Show more' da 16ª página clicado pela 6ª vez
2023-09-23 15:02:21,403 - INFO - Link 'Show more' da 16ª página clicado pela 7ª vez
2023-09-23 15:02:26,458 - INFO - Link 'Show more' da 16ª página clicado pela 8ª vez
2023-09-23 15:02:31,510 - INFO - Link 'Show more' da 16ª pági

2023-09-23 15:09:58,755 - INFO - Link 'Show more' da 30ª página clicado pela 2ª vez
2023-09-23 15:10:03,804 - INFO - Link 'Show more' da 30ª página clicado pela 3ª vez
2023-09-23 15:10:14,254 - INFO - Fim da página alcançado!
2023-09-23 15:10:14,428 - INFO - Foram coletados 170 id's de usuários da página completa.
Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...:   0%| | 30/35249 [15:54<359:27:04, 36.2023-09-23 15:10:21,372 - INFO - Link 'Show more' da 31ª página clicado pela 1ª vez
2023-09-23 15:10:26,424 - INFO - Link 'Show more' da 31ª página clicado pela 2ª vez
2023-09-23 15:10:31,476 - INFO - Link 'Show more' da 31ª página clicado pela 3ª vez
2023-09-23 15:10:36,522 - INFO - Link 'Show more' da 31ª página clicado pela 4ª vez
2023-09-23 15:10:41,583 - INFO - Link 'Show more' da 31ª página clicado pela 5ª vez
2023-09-23 15:10:46,631 - INFO - Link 'Show more' da 31ª página clicado pela 6ª vez
2023-09-23 15:10:51,680 - INFO - Link 'Show more' da 31ª pági

2023-09-23 15:17:25,662 - INFO - Foram coletados 16 id's de usuários da página completa.
Coletando os IDs de usuários que interagiram com todas as cervejas coletadas...:   0%| | 43/35249 [23:06<225:24:18, 23.2023-09-23 15:17:32,523 - INFO - Link 'Show more' da 44ª página clicado pela 1ª vez
2023-09-23 15:17:37,568 - INFO - Link 'Show more' da 44ª página clicado pela 2ª vez
2023-09-23 15:17:42,613 - INFO - Link 'Show more' da 44ª página clicado pela 3ª vez
2023-09-23 15:17:47,659 - INFO - Link 'Show more' da 44ª página clicado pela 4ª vez
2023-09-23 15:17:52,706 - INFO - Link 'Show more' da 44ª página clicado pela 5ª vez
2023-09-23 15:17:57,757 - INFO - Link 'Show more' da 44ª página clicado pela 6ª vez
2023-09-23 15:18:02,817 - INFO - Link 'Show more' da 44ª página clicado pela 7ª vez
2023-09-23 15:18:07,875 - INFO - Link 'Show more' da 44ª página clicado pela 8ª vez
2023-09-23 15:18:12,930 - INFO - Link 'Show more' da 44ª página clicado pela 9ª vez
2023-09-23 15:18:17,985 - INFO - Lin

2023-09-23 15:24:37,171 - INFO - Link 'Show more' da 60ª página clicado pela 2ª vez
2023-09-23 15:24:42,217 - INFO - Link 'Show more' da 60ª página clicado pela 3ª vez
2023-09-23 15:24:47,272 - INFO - Link 'Show more' da 60ª página clicado pela 4ª vez
2023-09-23 15:24:52,324 - INFO - Link 'Show more' da 60ª página clicado pela 5ª vez
2023-09-23 15:24:57,373 - INFO - Link 'Show more' da 60ª página clicado pela 6ª vez
2023-09-23 15:25:02,429 - INFO - Link 'Show more' da 60ª página clicado pela 7ª vez
2023-09-23 15:25:07,482 - INFO - Link 'Show more' da 60ª página clicado pela 8ª vez
2023-09-23 15:25:12,535 - INFO - Link 'Show more' da 60ª página clicado pela 9ª vez
2023-09-23 15:25:17,581 - INFO - Link 'Show more' da 60ª página clicado pela 10ª vez
2023-09-23 15:25:22,635 - INFO - Link 'Show more' da 60ª página clicado pela 11ª vez
2023-09-23 15:25:33,093 - INFO - Fim da página alcançado!
2023-09-23 15:25:33,586 - INFO - Foram coletados 338 id's de usuários da página completa.
Coletando 

...

2023-09-27 01:20:26,351 - INFO - Link 'Show more' da 7419ª página clicado pela 775ª vez
2023-09-27 01:20:31,434 - INFO - Link 'Show more' da 7419ª página clicado pela 776ª vez
2023-09-27 01:20:36,516 - INFO - Link 'Show more' da 7419ª página clicado pela 777ª vez
2023-09-27 01:20:41,602 - INFO - Link 'Show more' da 7419ª página clicado pela 778ª vez
2023-09-27 01:20:46,690 - INFO - Link 'Show more' da 7419ª página clicado pela 779ª vez
2023-09-27 01:20:51,779 - INFO - Link 'Show more' da 7419ª página clicado pela 780ª vez
2023-09-27 01:20:56,874 - INFO - Link 'Show more' da 7419ª página clicado pela 781ª vez
2023-09-27 01:21:01,963 - INFO - Link 'Show more' da 7419ª página clicado pela 782ª vez
2023-09-27 01:21:07,059 - INFO - Link 'Show more' da 7419ª página clicado pela 783ª vez
2023-09-27 01:21:12,161 - INFO - Link 'Show more' da 7419ª página clicado pela 784ª vez
2023-09-27 01:21:17,247 - INFO - Link 'Show more' da 7419ª página clicado pela 785ª vez
2023-09-27 01:21:22,339 - INFO -

2023-09-27 01:28:31,749 - INFO - Link 'Show more' da 7419ª página clicado pela 869ª vez
2023-09-27 01:28:37,003 - INFO - Link 'Show more' da 7419ª página clicado pela 870ª vez
2023-09-27 01:28:42,175 - INFO - Link 'Show more' da 7419ª página clicado pela 871ª vez
2023-09-27 01:28:47,481 - INFO - Link 'Show more' da 7419ª página clicado pela 872ª vez
2023-09-27 01:28:52,666 - INFO - Link 'Show more' da 7419ª página clicado pela 873ª vez
2023-09-27 01:28:57,982 - INFO - Link 'Show more' da 7419ª página clicado pela 874ª vez
2023-09-27 01:29:03,165 - INFO - Link 'Show more' da 7419ª página clicado pela 875ª vez
2023-09-27 01:29:08,476 - INFO - Link 'Show more' da 7419ª página clicado pela 876ª vez
2023-09-27 01:29:13,655 - INFO - Link 'Show more' da 7419ª página clicado pela 877ª vez
2023-09-27 01:29:18,843 - INFO - Link 'Show more' da 7419ª página clicado pela 878ª vez
2023-09-27 01:29:24,155 - INFO - Link 'Show more' da 7419ª página clicado pela 879ª vez
2023-09-27 01:29:29,346 - INFO -

2023-09-27 01:36:50,643 - INFO - Link 'Show more' da 7419ª página clicado pela 963ª vez
2023-09-27 01:36:55,926 - INFO - Link 'Show more' da 7419ª página clicado pela 964ª vez
2023-09-27 01:37:01,230 - INFO - Link 'Show more' da 7419ª página clicado pela 965ª vez
2023-09-27 01:37:06,520 - INFO - Link 'Show more' da 7419ª página clicado pela 966ª vez
2023-09-27 01:37:12,194 - INFO - Link 'Show more' da 7419ª página clicado pela 967ª vez
2023-09-27 01:37:17,496 - INFO - Link 'Show more' da 7419ª página clicado pela 968ª vez
2023-09-27 01:37:22,788 - INFO - Link 'Show more' da 7419ª página clicado pela 969ª vez
2023-09-27 01:37:28,081 - INFO - Link 'Show more' da 7419ª página clicado pela 970ª vez
2023-09-27 01:37:34,038 - INFO - Link 'Show more' da 7419ª página clicado pela 971ª vez
2023-09-27 01:37:39,588 - INFO - Link 'Show more' da 7419ª página clicado pela 972ª vez
2023-09-27 01:37:44,892 - INFO - Link 'Show more' da 7419ª página clicado pela 973ª vez
2023-09-27 01:37:50,571 - INFO -

2023-09-27 01:45:23,663 - INFO - Link 'Show more' da 7419ª página clicado pela 1056ª vez
2023-09-27 01:45:31,131 - INFO - Link 'Show more' da 7419ª página clicado pela 1057ª vez
2023-09-27 01:45:36,535 - INFO - Link 'Show more' da 7419ª página clicado pela 1058ª vez
2023-09-27 01:45:42,109 - INFO - Link 'Show more' da 7419ª página clicado pela 1059ª vez
2023-09-27 01:45:47,525 - INFO - Link 'Show more' da 7419ª página clicado pela 1060ª vez
2023-09-27 01:45:52,926 - INFO - Link 'Show more' da 7419ª página clicado pela 1061ª vez
2023-09-27 01:46:00,756 - INFO - Link 'Show more' da 7419ª página clicado pela 1062ª vez
2023-09-27 01:46:06,251 - INFO - Link 'Show more' da 7419ª página clicado pela 1063ª vez
2023-09-27 01:46:11,658 - INFO - Link 'Show more' da 7419ª página clicado pela 1064ª vez
2023-09-27 01:46:17,553 - INFO - Link 'Show more' da 7419ª página clicado pela 1065ª vez
2023-09-27 01:46:23,001 - INFO - Link 'Show more' da 7419ª página clicado pela 1066ª vez
2023-09-27 01:46:28,4

TimeoutException: Message: timeout: Timed out receiving message from renderer: 300.000
  (Session info: chrome=116.0.5845.188)
Stacktrace:
	GetHandleVerifier [0x00007FF72D4052A2+57122]
	(No symbol) [0x00007FF72D37EA92]
	(No symbol) [0x00007FF72D24E3AB]
	(No symbol) [0x00007FF72D23C01A]
	(No symbol) [0x00007FF72D23BF63]
	(No symbol) [0x00007FF72D23A9E5]
	(No symbol) [0x00007FF72D23B31E]
	(No symbol) [0x00007FF72D2480CB]
	(No symbol) [0x00007FF72D257F31]
	(No symbol) [0x00007FF72D25C0DA]
	(No symbol) [0x00007FF72D23B8E7]
	(No symbol) [0x00007FF72D257E0A]
	(No symbol) [0x00007FF72D2BEAAF]
	(No symbol) [0x00007FF72D2A6DB3]
	(No symbol) [0x00007FF72D27D2B1]
	(No symbol) [0x00007FF72D27E494]
	GetHandleVerifier [0x00007FF72D6AEF82+2849794]
	GetHandleVerifier [0x00007FF72D701D24+3189156]
	GetHandleVerifier [0x00007FF72D6FACAF+3160367]
	GetHandleVerifier [0x00007FF72D496D06+653702]
	(No symbol) [0x00007FF72D38A208]
	(No symbol) [0x00007FF72D3862C4]
	(No symbol) [0x00007FF72D3863F6]
	(No symbol)

In [40]:
len(all_users)

92326

In [41]:
path = '../data/'
user_links_json = {'user IDs': sorted(all_users)}
file_name = 'alternative_approach_user_IDs.json'
logger.info('Foram coletadas apenas 21% das páginas de cervejas :(')
logger.info('Exportando a lista de usuários coletados na forma de um JSON...')
export_json(user_links_json, path + file_name)
logger.info('Exportado!')

2023-09-27 11:25:49,792 - INFO - Foram coletadas apenas 21% das páginas de cervejas :(
2023-09-27 11:25:49,795 - INFO - Exportando a lista de usuários coletados na forma de um JSON...
2023-09-27 11:25:49,899 - INFO - Exportado!
